In [1]:
import numpy
import pickle
import random

## store impl in imdb

In [2]:
in_dir = 'data/imdb/'
out_dir = 'data/imdb_imps/'
file = 'train'

In [5]:
imps = pickle.load(open(out_dir+'vqa_'+file+'_imps.pkl','rb'))
imdb_ori = numpy.load(in_dir+'imdb_'+file+'2014.npy',allow_pickle=True)

In [ ]:
for i in range(1,len(imdb_ori)):
    key = imdb_ori[i]['question_id']
    if sum([len(v) for v in imps[key].values()])==0:
        imdb_ori[i]['is_imps'] = False
    else:
        imdb_ori[i]['is_imps'] = True
        imdb_ori[i]['qa_implications'] = imps[key]

In [ ]:
pickle.dump(imdb_ori,open(out_dir+'imdb_'+file+'2014.npy','wb'))

## tokenizing qa_imps and deleting entries w/o imps

In [ ]:
from dataset_utils import text_processing

In [ ]:
imdb = numpy.load(out_dir+'imdb_'+file+'2014.npy',allow_pickle=True)
imdb_ori = numpy.load(in_dir+'imdb_'+file+'2014.npy',allow_pickle=True)

In [ ]:
# tokenize and delete previous keys

for i in range(1,len(imdb)):
    if imdb[i]['is_imps']:
        qa = imdb[i]['qa_implications']
        imdb[i]['qa_tokens']={}
        imdb[i]['qa_answers']={}
        for key in qa.keys():
            imdb[i]['qa_tokens'][key] = []
            imdb[i]['qa_answers'][key] = []
            for imp in qa[key]:
                imdb[i]['qa_tokens'][key].append(text_processing.tokenize(imp[0]))
                imdb[i]['qa_answers'][key].append(imp[1])
        imdb[i].pop('qa_implications',None)

In [ ]:
# delete questions w/o any implications for all valid answers

idx = []
for i in range(1,len(imdb)):
    if not imdb[i]['is_imps']:
        idx.append(i)
    imdb[i].pop('is_imps')

imdb = numpy.delete(imdb,idx)

In [ ]:
# delete questions w/o implications for any valid answers

idx = []
for i in range(1,len(imdb)):
    qa = imdb[i]['qa_answers']
    for key in qa.keys():
        if len(qa[key])==0 :
            idx.append(i)
            break

imdb = numpy.delete(imdb,idx)

In [ ]:
pickle.dump(imdb,open(out_dir+'imdb_'+file+'2014.npy','wb'))

## Dataset analysis

In [2]:
import json
in_dir = 'data/imdb/'
out_dir = 'data/imdb_imps/'
file = 'train'
imdb = numpy.load(out_dir+'imdb_'+file+'2014.npy',allow_pickle=True)
imdb_ori = numpy.load(in_dir+'imdb_'+file+'2014.npy',allow_pickle=True)
q = json.load(open('orig_data/vqa_v2.0/v2_mscoco_'+file+'2014_annotations.json','rb'))

In [17]:
question_types = {}
qmap = {}

for ann in q['annotations']:
    atype = ann['answer_type']
    qid = ann['question_id']
    qmap[qid] = atype
    if atype not in question_types.keys():
        question_types[atype] = []
    question_types[atype].append(qid)

In [20]:
print('Stats original vqa2.0')
for key in question_types.keys():
    print('%s lenght: %d percentage: %.2f' % (key,len(question_types[key]),100*len(question_types[key])/len(q['annotations'])))

Stats original vqa2.0
other lenght: 219269 percentage: 49.41
yes/no lenght: 166882 percentage: 37.61
number lenght: 57606 percentage: 12.98


In [18]:
updated_question_types = {}

for ann in imdb[1:]:
    qid = ann['question_id']
    atype = qmap[qid]
    
    if atype not in updated_question_types.keys():
        updated_question_types[atype]=[]
    updated_question_types[atype].append(qid)

In [22]:
print('Stats new dataset:')
for key,val in updated_question_types.item():
    print('%s lenght: %d percentage: %.2f' % (key,len(updated_question_types[key]),100*len(updated_question_types[key])/len(imdb)))

print()

Stats new dataset:


AttributeError: 'dict' object has no attribute 'item'

In [24]:
updated_question_types.items()

dict_items([('other', [458752000, 458752001, 458752002, 262146000, 262146001, 262146002, 524291000, 524291002, 393221002, 393223001, 393223002, 393224001, 524297001, 393227001, 393227003, 131084000, 131084002, 131074000, 131074004, 393230000, 393230003, 393230004, 393230005, 393230007, 393230009, 131087000, 131087004, 131075000, 131075002, 131075007, 131075008, 131075009, 131075010, 131075012, 131075013, 131075014, 137045000, 137045002, 524311000, 524311002, 25000, 25001, 25004, 25006, 25010, 524314002, 262171001, 262171002, 262172000, 262172001, 131101000, 30001, 30004, 240304000, 240304002, 34001, 393251002, 393251003, 262180000, 262180002, 262180003, 524325001, 43697001, 43697005, 43697006, 262184001, 262184002, 131113000, 131113002, 131113003, 262187001, 262187002, 262191001, 262191002, 49001, 524338001, 213863000, 213863001, 213863002, 393268000, 393268001, 393268002, 131126000, 131127000, 131128000, 131128001, 262201000, 262201002, 370986000, 262204001, 262204002, 131133000, 1311

## playground

In [69]:
yesno_qid = (ann['question_id'] for ann in q['annotations'] if ann['answer_type']=='yes/no')

In [79]:
final = []
for idx in yesno_qid:
    if 0 not in [len(i) for i in imps[idx].values()]:
        final.append(idx)

In [89]:
for ann in imdb[1:10000]:
    qid = ann['question_id']
    if qid in final:
        print(ann['question_str'],imps[qid])

Is the man riding on a dirt path? {'yes': [('Is the man riding on a path?', 'yes', 'remove_modifier')]}
Is it a clear day? {'yes': [('Is it a day?', 'yes', 'remove_modifier')]}
Is the man having a good time? {'yes': [('Is the man having a bad time?', 'no', 'wordnet_adj_mutex'), ('Is the man having a time?', 'yes', 'remove_modifier')]}
Is this a good dessert? {'yes': [('Is this a bad dessert?', 'no', 'wordnet_adj_mutex'), ('Is this a dessert?', 'yes', 'remove_modifier')]}
Is this a hot dog? {'yes': [('Is this a cold dog?', 'no', 'wordnet_adj_mutex'), ('Is this a dog?', 'yes', 'remove_modifier')]}
Is there a flower arrangement on the lawn? {'yes': [('Is there an arrangement on the lawn?', 'yes', 'remove_modifier')]}
Are the mountains high? {'yes': [('Are the mountains low ?', 'no', 'wordnet_adj_mutex')]}
Is there a big tree behind the clock? {'yes': [('Is there a tree behind the clock?', 'yes', 'remove_modifier')]}
Does this photo show train tracks? {'yes': [('Does this photo show tracks

Is the sky cloudy? {'yes': [('Is the sky clear ?', 'no', 'wordnet_adj_mutex')]}
Is this a heavy vehicle? {'yes': [('Is this a light vehicle?', 'no', 'wordnet_adj_mutex'), ('Is this a vehicle?', 'yes', 'remove_modifier')]}
Is this a large crowd? {'yes': [('Is this a small crowd?', 'no', 'wordnet_adj_mutex'), ('Is this a crowd?', 'yes', 'remove_modifier')]}
Are the women in the front wearing cheerful outfits? {'yes': [('Are the women in the back wearing cheerful outfits?', 'no', 'wordnet_adj_mutex'), ('Are the women in the front wearing depressing outfits?', 'no', 'wordnet_adj_mutex'), ('Are the women in the front wearing outfits?', 'yes', 'remove_modifier')]}
Can this man get the oven as clean as it should be? {'yes': [('Can this man get the oven as dirty as it should be?', 'no', 'wordnet_adj_mutex')]}
Is this person warm? {'yes': [('Is this person cool ?', 'no', 'wordnet_adj_mutex')]}
Is it cold out? {'yes': [('Is it hot out?', 'no', 'wordnet_adj_mutex')]}
Are there leather straps arou

Is he ready for the ball? {'yes': [('Is he unready for the ball?', 'no', 'wordnet_adj_mutex')]}
Does anything in this picture have aluminum foil on it? {'yes': [('Does anything in this picture have foil on it?', 'yes', 'remove_modifier')]}
Is this an industrial area? {'yes': [('Is this a nonindustrial area?', 'no', 'wordnet_adj_mutex'), ('Is this an area?', 'yes', 'remove_modifier')]}
Are these vegetable fresh? {'yes': [('Are these vegetable salty ?', 'no', 'wordnet_adj_mutex')]}
Is this picture black and white? {'yes': [('Is this picture white and white?', 'no', 'wordnet_adj_mutex'), ('Is this picture black and black ?', 'no', 'wordnet_adj_mutex')]}
Is it a sunny day? {'yes': [('Is it a day?', 'yes', 'remove_modifier')]}
Do you see a fire hydrant? {'yes': [('Do you see a hydrant?', 'yes', 'remove_modifier')]}
Is it a hot day? {'yes': [('Is it a cold day?', 'no', 'wordnet_adj_mutex'), ('Is it a day?', 'yes', 'remove_modifier')]}
Is this a healthy dish? {'yes': [('Is this an unhealthy d

Could this plane be military? {'yes': [('Could this plane be civilian ?', 'no', 'wordnet_adj_mutex')]}
Is the luggage full? {'yes': [('Is the luggage empty ?', 'no', 'wordnet_adj_mutex')]}
Can you  spot mountains? {'yes': [('Can you   mountains?', 'yes', 'remove_modifier')]}
Is this a color photo? {'yes': [('Is this a photo?', 'yes', 'remove_modifier')]}
Is this man happy? {'yes': [('Is this man unhappy ?', 'no', 'wordnet_adj_mutex')]}
Is she happy? {'yes': [('Is she unhappy ?', 'no', 'wordnet_adj_mutex')]}
Is this a restaurant kitchen? {'yes': [('Is this a kitchen?', 'yes', 'remove_modifier')]}
Is a shower curtain visible? {'yes': [('Is a shower curtain invisible ?', 'no', 'wordnet_adj_mutex'), ('Is a curtain visible?', 'yes', 'remove_modifier')]}
Is it a good idea for this person to be wearing a helmet? {'yes': [('Is it a bad idea for this person to be wearing a helmet?', 'no', 'wordnet_adj_mutex'), ('Is it an idea for this person to be wearing a helmet?', 'yes', 'remove_modifier')]}

Is one of the players wearing green shorts? {'yes': [('Is one of the players wearing shorts?', 'yes', 'remove_modifier')]}
Is he doing a dangerous jump? {'yes': [('Is he doing a safe jump?', 'no', 'wordnet_adj_mutex'), ('Is he doing a jump?', 'yes', 'remove_modifier')]}
Is the dog happy on the table? {'yes': [('Is the dog unhappy on the table?', 'no', 'wordnet_adj_mutex')]}
Is this a professional event? {'yes': [('Is this a nonprofessional event?', 'no', 'wordnet_adj_mutex'), ('Is this an event?', 'yes', 'remove_modifier')]}
Is the zebra alert? {'yes': [('Is the alert?', 'yes', 'remove_modifier')]}
Is the bus old? {'yes': [('Is the bus new ?', 'no', 'wordnet_adj_mutex')]}
Is this a lonely area? {'yes': [('Is this an area?', 'yes', 'remove_modifier')]}
Does this look like a fresh fruit stand? {'yes': [('Does this look like a salty fruit stand?', 'no', 'wordnet_adj_mutex'), ('Does this look like a fresh stand?', 'yes', 'remove_modifier'), ('Does this look like a fruit stand?', 'yes', 're

...

Is it cold in this picture? {'yes': [('Is it hot in this picture?', 'no', 'wordnet_adj_mutex')]}
Might one assume that this stance shows a willingness to take up space and assert authority? {'yes': [('Might one assume that this stance shows a willingness to take up space and authority?', 'yes', 'remove_modifier')]}
Is this a real person? {'yes': [('Is this a person?', 'yes', 'remove_modifier')]}
Would a cautious person wear leather pants to ride this? {'yes': [('Would a cautious person wear pants to ride this?', 'yes', 'remove_modifier'), ('Would a person wear leather pants to ride this?', 'yes', 'remove_modifier')]}
Is it a cloudy day? {'yes': [('Is it a clear day?', 'no', 'wordnet_adj_mutex'), ('Is it a day?', 'yes', 'remove_modifier')]}
Is he a frisbee player? {'yes': [('Is he a player?', 'yes', 'remove_modifier')]}
Is this a grass court? {'yes': [('Is this a court?', 'yes', 'remove_modifier')]}
Is this man riding a white surfboard? {'yes': [('Is this man riding a black surfboard?',

Is the elephant's trunk point upward? {'yes': [("Is the elephant's point upward?", 'yes', 'remove_modifier')]}
Does the stop sign reflect in the water? {'yes': [('Does the sign reflect in the water?', 'yes', 'remove_modifier')]}
Is the building on the left tall? {'yes': [('Is the building on the right tall?', 'no', 'wordnet_adj_mutex'), ('Is the building on the left short ?', 'no', 'wordnet_adj_mutex')]}
Is this person getting ready to travel? {'yes': [('Is this person getting unready to travel?', 'no', 'wordnet_adj_mutex')]}
Are the bed frames wooden? {'yes': [('Are the frames wooden?', 'yes', 'remove_modifier')]}
Are these real birds? {'yes': [('Are these birds?', 'yes', 'remove_modifier')]}
Is the shower curtain open? {'yes': [('Is the shower curtain closed ?', 'no', 'wordnet_adj_mutex')]}
Is this bus a large one? {'yes': [('Is this bus a small one?', 'no', 'wordnet_adj_mutex')]}
Is the man wearing a wedding ring? {'yes': [('Is the man wearing a ring?', 'yes', 'remove_modifier')]}
I

Is this a vegetarian pizza? {'yes': [('Is this a pizza?', 'yes', 'remove_modifier')]}
Does the frosting show? {'yes': [('Does the show?', 'yes', 'remove_modifier')]}
Are there heat lamps? {'yes': [('Are there lamps?', 'yes', 'remove_modifier')]}
Are two people wearing similar patterns? {'yes': [('Are two people wearing unlike patterns?', 'no', 'wordnet_adj_mutex'), ('Are two people wearing patterns?', 'yes', 'remove_modifier')]}
Is this a sleek design? {'yes': [('Is this a design?', 'yes', 'remove_modifier')]}
Is it a warm day? {'yes': [('Is it a cool day?', 'no', 'wordnet_adj_mutex'), ('Is it a day?', 'yes', 'remove_modifier')]}
Is it cold here? {'yes': [('Is it hot here?', 'no', 'wordnet_adj_mutex')]}
Does the keyboard have a number pad? {'yes': [('Does the keyboard have a pad?', 'yes', 'remove_modifier')]}
Is this picnic food? {'yes': [('Is this food?', 'yes', 'remove_modifier')]}
Is this homemade? {'yes': [('Is this factory-made ?', 'no', 'wordnet_adj_mutex')]}
Is the water cold? {

Is there anything at all out of the ordinary in this scene? {'yes': [('Is there anything at all out of the extraordinary in this scene?', 'no', 'wordnet_adj_mutex')]}
Is someone in the driver seat? {'yes': [('Is someone in the seat?', 'yes', 'remove_modifier')]}
Is this a clean kitchen? {'yes': [('Is this a dirty kitchen?', 'no', 'wordnet_adj_mutex'), ('Is this a kitchen?', 'yes', 'remove_modifier')]}
Is the door open? {'yes': [('Is the door closed ?', 'no', 'wordnet_adj_mutex')]}
Is there a yield sign? {'yes': [('Is there a sign?', 'yes', 'remove_modifier')]}
Does his tie have a plaid pattern? {'yes': [('Does his tie have a pattern?', 'yes', 'remove_modifier')]}
Is someone asleep on the bench? {'yes': [('Is someone awake on the bench?', 'no', 'wordnet_adj_mutex')]}
Is there snow on the ground under the stop sign? {'yes': [('Is there snow on the ground under the sign?', 'yes', 'remove_modifier')]}
Is the clock old? {'yes': [('Is the clock new ?', 'no', 'wordnet_adj_mutex')]}
Is the wom

Is the big elephant asleep? {'yes': [('Is the big elephant awake ?', 'no', 'wordnet_adj_mutex'), ('Is the elephant asleep?', 'yes', 'remove_modifier')]}
Could the dogs be hungry? {'yes': [('Could the dogs be thirsty ?', 'no', 'wordnet_adj_mutex')]}
Does the man have any facial hair? {'yes': [('Does the man have any hair?', 'yes', 'remove_modifier')]}
Is there toilet paper here? {'yes': [('Is there paper here?', 'yes', 'remove_modifier')]}
Is this hot dog high in sodium? {'yes': [('Is this hot dog low in sodium?', 'no', 'wordnet_adj_mutex'), ('Is this dog high in sodium?', 'yes', 'remove_modifier')]}
Are there any condiments on this hot dog? {'yes': [('Are there any condiments on this cold dog?', 'no', 'wordnet_adj_mutex'), ('Are there any condiments on this dog?', 'yes', 'remove_modifier')]}
Is this a thin crust? {'yes': [('Is this a full crust?', 'no', 'wordnet_adj_mutex'), ('Is this a crust?', 'yes', 'remove_modifier')]}
IS the floor shiny? {'yes': [('IS the floor unglazed ?', 'no', 

In [65]:
len(imdb_ori),len(imdb),total_yesno,count

(443758, 263331, 166882, 121769)

In [67]:
total_yesno/len(imdb_ori),(total_yesno-count)/len(imdb)

(0.3760653329066744, 0.1713167078695634)

In [2]:
import sys
sys.path.append('/home/btp/pg_aa_1/.conda/envs/test/lib/python3.8/site-packages/tensorboardX-1.2-py3.8.egg/')

In [ ]:
from torch.utils.data import DataLoader
from train_model.dataset_utils import prepare_test_data_set,prepare_eval_data_set,prepare_train_data_set
import torch
from train_model.helper import run_model, print_result, build_model
from config.config_utils import finalize_config
from config.config import cfg

config_file = 'results/pythia_cycle_consistent/2020/config.yaml'
model_file = 'results/pythia_cycle_consistent/2020/best_model.pth'
finalize_config(cfg, config_file, None)

batch_size = cfg['data']['batch_size']

data= prepare_train_data_set(**cfg['data'], **cfg['model'], verbose=True)

/home1/BTP/pg_aa_1/btp/config/config_utils.py:86: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  updates = yaml.load(f)


In [22]:

cfg['data']['imdb_file_train'] = ['imdb_imps/imdb_val2train2014.npy']
cfg['data']['image_feat_train'] = ['detectron_fix_100/fc6/vqa/val2014']

In [14]:
a

NameError: name 'a' is not defined

In [ ]:
c=0
while(c<10000):
    c+=1
    try:
        print(data_set_test[4])
    except:
        continue

In [21]:
data_reader_test = DataLoader(data, shuffle=True, batch_size=2, num_workers=1,drop_last=True)
for idx,batch in enumerate(data_reader_test):
    print(idx)

KeyError: Caught KeyError in DataLoader worker process 0.
Original Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/torch/utils/data/_utils/worker.py", line 178, in _worker_loop
    data = fetcher.fetch(index)
  File "/opt/anaconda3/lib/python3.7/site-packages/torch/utils/data/_utils/fetch.py", line 47, in fetch
    return self.collate_fn(data)
  File "/opt/anaconda3/lib/python3.7/site-packages/torch/utils/data/_utils/collate.py", line 74, in default_collate
    return {key: default_collate([d[key] for d in batch]) for key in elem}
  File "/opt/anaconda3/lib/python3.7/site-packages/torch/utils/data/_utils/collate.py", line 74, in <dictcomp>
    return {key: default_collate([d[key] for d in batch]) for key in elem}
  File "/opt/anaconda3/lib/python3.7/site-packages/torch/utils/data/_utils/collate.py", line 74, in default_collate
    return {key: default_collate([d[key] for d in batch]) for key in elem}
  File "/opt/anaconda3/lib/python3.7/site-packag

In [17]:
for idx in [0,1,2,3]:
    yield data_reader_test.collate_fn(data[idx])

SyntaxError: 'yield' outside function (<ipython-input-17-b86a004ba169>, line 2)

In [21]:
len(data_reader_test),batch_size*16

(38494, 4096)

# Generated Questions

In [97]:
gq = numpy.load("/home1/BTP/pg_aa_1/btp/boards/pythia_cycle_consistent/2020/gq_42000.npy", allow_pickle=True)

In [106]:
gq.all()['annotations'][:10],gq.all()['answers'][:10]

([{'image_id': 262162,
   'caption': '<start> is there a bedroom <end> <unk> <end> <end> <end> <end> <end> <end> <end>'},
  {'image_id': 262162,
   'caption': '<start> is there anything white in <end> <end> <end> <end> <end> <end> <end> <end>'},
  {'image_id': 262162,
   'caption': '<start> are there any pictures on the <end> <unk> <end> <unk> <end> <end> <end>'},
  {'image_id': 262162,
   'caption': '<start> are any pictures on the wall <unk> <end> <unk> <end> <unk> <end> <end>'},
  {'image_id': 262162,
   'caption': '<start> is the chair black <unk> <end> <end> <unk> <end> <end> <end> <end> <end>'},
  {'image_id': 262162,
   'caption': '<start> is this a bedroom <end> <unk> <end> <unk> <end> <end> <end> <end> remainder'},
  {'image_id': 262162,
   'caption': '<start> is this a kitchen <end> <unk> <unk> <end> <end> <end> <end> <end> <end>'},
  {'image_id': 262162,
   'caption': '<start> is there a chair in the picture <unk> <unk> <unk> <unk> <unk> <unk>'},
  {'image_id': 262162,
   'c